In [ ]:
# ..... build coexp nets? ..... #

In [2]:
library(SingleCellExperiment)
library(SummarizedExperiment)
library(scater)
library(Seurat)
library(dplyr)
library(scran)

In [59]:
## create bulk samples from cluster-specific sc data ##
get_bulk_samples <- function(mat, number_of_samples){
    nsamples = round(dim(mat)[2]/number_of_samples)    # divide into samples of ~20 cells each
    bulk_samples = matrix(NA, nrow = dim(mat)[1], ncol = nsamples)
    
    if(nsamples==1){
        bulk_samples[,1] = rowSums(mat)
    }else{
        for(ii in 1:(nsamples-1)){      
            ids = sample(dim(mat)[2], number_of_samples, replace = FALSE)
            bulk_samples[,ii] = rowSums(mat[,ids])
            mat <- mat[,-ids]        
        }
    }
    bulk_samples[,nsamples] = rowSums(mat)    
    rownames(bulk_samples) = rownames(mat)
    return(bulk_samples)
}

## create coexpression network ## 
build_coexp_network <- function(net, method = "spearman", flag = "rank"){
    
    # Calculate correlation coefficients
    genes = rownames(net)
    net = net[rowSums(net) > 0, ]

#     print(paste0("... ",dim(net)[1]," of ",length(genes), " genes have non-zero expression" ))

    net = cor(t(net), method = method)
    
    # Create network
    temp = net[upper.tri(net, diag = T)]
    if (flag == "abs"){
        temp = abs(temp)
    }
    
#     print("...ranking")
    temp = rank(temp, ties.method = "average")  

#     print("...reconstructing matrix")
    net[upper.tri(net, diag = T)] = temp

    net = t(net)
    net[upper.tri(net, diag = T)] = temp

    net = net / max(net, na.rm = T)
    med = median(net, na.rm = T)

    ind = setdiff(genes, rownames(net))   # which genes are missing?

    temp = matrix(med, length(ind), dim(net)[2])
    rownames(temp) = ind

    net = rbind(net, temp)
    temp = matrix(med, dim(net)[1], length(ind))
    colnames(temp) = ind
    net = cbind(net, temp)

    # reorder to original
    net = net[genes, genes]
    diag(net) = 1

    return(net)
}

# rank-standardize
get_rankstd <- function(aggNet){
    temp = aggNet[upper.tri(aggNet, diag = T)]
    temp = rank(temp, ties.method = "average")  
    aggNet[upper.tri(aggNet, diag = T)] = temp
    aggNet = t(aggNet)
    aggNet[upper.tri(aggNet, diag = T)] = temp
    aggNet = aggNet / max(aggNet, na.rm = T)
    return(aggNet)
}

In [3]:
# load data
get_seurat_obj <- function(currstage1){
    
    sc1 = readRDS(paste0(currstage1, '_integrated_cca.rds'))

#     df1 = read.delim(paste0(currstage1, '_cluster_anno_Knight-Schrijver.csv'), sep = ',')
    df1 = read.delim(paste0(currstage1, '_Qiu_SHC_Monocle_clusters.csv'), sep = ',')
    
    ids = match(rownames(sc1@meta.data), df1$barcode)
    
#     sc1$metacell = df1$metacell[ids]
#     sc1$celltype = df1$consensus_type[ids]
#     sc1$cluster = df1$cluster[ids]
    
    sc1$celltype = df1$monocle_cluster[ids]
    sc1$celltype <- paste0(sc1$sample, '|', sc1$celltype)
    sc1$class = df1$class[ids]
    sc1$subclass = df1$celltype[ids]
    sc1$subclass2 = df1$final_celltype[ids]
    sc1$monocle_label = df1$monocle_label[ids]
    
    df2 = read.delim(paste0(currstage1, '_monocle_matched_clusters.csv'), sep = ',')
    sc1$cluster = df2$cluster[match(sc1$celltype, df2$metacell)]

    sc1$stage <- sc1$orig.ident
    sc1 <- sc1[,!is.na(sc1$celltype)]
    return(sc1)
}

In [49]:
# load individual sample files
stage1 = 'stage32'
sc1 = get_seurat_obj(stage1)

In [50]:
# SCE object
sce = SingleCellExperiment(list(counts = sc1@assays$RNA@counts), colData = DataFrame(sc1@meta.data))
sce <- logNormCounts(sce)

In [51]:
hvgs <- getTopHVGs(sce, n = 6000)
length(hvgs)

[1] 6000

In [52]:
# threshold to top 4k genes expressed in at least 25k cells
sce <- sce[hvgs,]
dim(sce)

[1]  6000 21401

In [53]:
cpm(sce) <- calculateCPM(sce)

In [61]:
# build bulk samples, and coexp networks from bulk samples
samples = unique(sce$sample)
cls_groups = unique(sce$cluster)
pb = txtProgressBar(min = 0, max = length(cls_groups), initial = 0)

for(ii in 1:length(samples)){
    
    sce2 <- sce[,sce$sample==samples[ii]]
    full_bulk = c()
    
    for(oo in 1:length(cls_groups)){
        
        currcls = cls_groups[oo]
        temp1 = cpm(sce2)[,sce2$cluster==currcls]
        sample_size = 20
        
        if(sum(sce2$cluster==currcls) >= sample_size){
            bulk1 = get_bulk_samples(temp1, sample_size)

            bulk1 = data.frame(bulk1)
            if(!length(full_bulk)){
                full_bulk = bulk1
            }else{
                full_bulk = cbind(full_bulk, bulk1)
            }
        }
        
        setTxtProgressBar(pb, oo)
    }
    
    cor1 = build_coexp_network(full_bulk, method = 'spearman')

    # save
    fileo = paste0(stage1, '_', ii, '_top6000.Rdata')
    save(cor1, file = fileo)
    
}

=====                                                                           ======================================================================================================================================================

In [62]:
cor1[100:103,100:103]

SASH1     WWOX      HS6ST3     TSHZ2     
SASH1  1.0000000 0.9992546 0.83516281 0.98050531
WWOX   0.9992546 1.0000000 0.23210722 0.99940053
HS6ST3 0.8351628 0.2321072 1.00000000 0.05985744
TSHZ2  0.9805053 0.9994005 0.05985744 1.00000000

In [63]:
# build aggregate network
stage1 = 'stage32'
pb = txtProgressBar(min = 0, max = 3, initial = 0)

for(oo in 1:3){

    fileo = paste0(stage1, '_', oo, '_top6000.Rdata')
    load(fileo)
    if(oo == 1){
        aggNet = cor1
    }else{
        aggNet = aggNet + cor1
    }
    setTxtProgressBar(pb, oo)
}

# rank-standardize
temp = aggNet[upper.tri(aggNet, diag = T)]
temp = rank(temp, ties.method = "average")  
aggNet[upper.tri(aggNet, diag = T)] = temp

aggNet = t(aggNet)
aggNet[upper.tri(aggNet, diag = T)] = temp
aggNet = aggNet / max(aggNet, na.rm = T)

fileo2 = paste0(stage1, '_sample_aggregate_top6000.Rdata')
save(aggNet, file = fileo2)

In [64]:
aggNet[100:103,100:103]

SASH1     WWOX      HS6ST3     TSHZ2     
SASH1  1.0000000 0.9995741 0.79369837 0.98230397
WWOX   0.9995741 1.0000000 0.10820850 0.99937442
HS6ST3 0.7936984 0.1082085 1.00000000 0.04180528
TSHZ2  0.9823040 0.9993744 0.04180528 1.00000000